In [ ]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

from numpy import mean
from numpy import std

from matplotlib import pyplot
from sklearn.metrics import accuracy_score,confusion_matrix,classification_report
from sklearn.preprocessing import QuantileTransformer
from sklearn.pipeline import Pipeline

from scipy.stats import mode

In [ ]:
!nvidia-smi  

Sun Jun 12 18:30:55 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   34C    P0    24W / 300W |      0MiB / 16160MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

In [ ]:
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [ ]:
#npz files can only be loaded using /gdrive path
from google.colab import drive
drive.mount('/content/gdrive')
#%cd /gdrive

Mounted at /content/gdrive


In [ ]:
!pip install mne

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 7.5 MB 15.7 MB/s 


In [ ]:
#import pyeeg
from tensorflow import keras 

In [ ]:
%matplotlib inline

import glob
import math
import ntpath
import random, os, sys
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns
#import edfreader
#import models
import mne
#import pyeeg
import warnings
warnings.filterwarnings('ignore')

from matplotlib.backends.backend_pdf import PdfPages
from mne.datasets.sleep_physionet._utils import _fetch_one, _data_path, AGE_SLEEP_RECORDS, _check_subjects
from datetime import datetime
from mne import Epochs, pick_types, find_events
from mne.io import concatenate_raws, read_raw_edf
from mne.time_frequency import psd_welch
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split
from tensorflow import keras

from tensorflow.keras.utils import to_categorical

from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, CSVLogger
import imblearn
from imblearn.over_sampling import SMOTE
from sklearn.svm import SVC
import joblib

from sklearn.metrics import make_scorer, f1_score, accuracy_score, classification_report, log_loss
from sklearn.metrics import roc_auc_score, confusion_matrix, roc_auc_score, roc_curve

from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
#from xgboost import XGBClassifier
#import xgboost

In [ ]:
VBS = True  # constant boolean to enable/disbale verbose
EPOCH_SEC_SIZE = 30  # Epoch duration selection
seed = 42  # seed value for the random seeds
batch_size = 64
number_of_files = 100 #100 npz files, 50 subjects, each suject has 2 nights, so 2 files per subject (50*2)=100

# values to label the stages
UNKNOWN = -1
W = 0
N1 = 1
N2 = 2
N3 = 3
REM = 4

# making string dictionary for the label values
label_dict = {
    "UNKNOWN"  : UNKNOWN,
    "W"        : W,
    "N1"       : N1,
    "N2"       : N2,
    "N3"       : N3,
    "REM"      : REM
}

# converting from label values to strings 
class_dict = {
    -1: "UNKNOWN",
    0 : "W",
    1 : "N1",
    2 : "N2",
    3 : "N3",
    4 : "REM"
}

# annotation dictionary to convert from string to label values
annot2label = {
    "Sleep stage ?": -1,
    "Movement time": -1,
    "Sleep stage W": 0,
    "Sleep stage 1": 1,
    "Sleep stage 2": 2,
    "Sleep stage 3": 3,
    "Sleep stage 4": 3,
    "Sleep stage R": 4
}
#project_path = os.path.abspath(os.getcwd())  # finding the current project path in windows

In [ ]:
from tensorflow.keras import optimizers, losses, activations, models
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from tensorflow.keras.layers import Input, Conv1D, Dense, Dropout, MaxPool1D, Activation
from tensorflow.keras.layers import Reshape, LSTM, TimeDistributed, Bidirectional, BatchNormalization, Flatten, RepeatVector
from tensorflow.keras.optimizers import Adam
#from keras_contrib.layers import CRF

from scipy.signal import butter, lfilter


In [ ]:
Fs = 100
from keras.utils import np_utils

In [ ]:
subject_466_df=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/subject_466_dataset.csv',header=None)

In [ ]:
x_sub_set=subject_466_df.drop([3000],axis=1)

In [ ]:
x_sub_set

0         1         2         3         4         5         6     \
0     0.093275 -0.180877 -0.033978  0.000849 -0.034871 -0.049605 -0.036210   
1    -0.099614 -0.188914 -0.078181 -0.035764 -0.118813 -0.025941 -0.074609   
2    -0.067465  0.003082  0.000849  0.005761 -0.160784 -0.325097 -0.310363   
3    -0.097381  0.036123 -0.029513 -0.051838 -0.020136 -0.023262 -0.087558   
4     0.097740  0.166948  0.161144  0.273662  0.258035  0.262946  0.345103   
...        ...       ...       ...       ...       ...       ...       ...   
4015  0.230809  0.187421  0.236835  0.135598  0.129973  0.151265  0.097433   
4016 -0.020677 -0.017061 -0.017463  0.024719 -0.007821 -0.023891 -0.026301   
4017  0.101048  0.097433  0.070918  0.067705  0.068106  0.066098  0.061277   
4018  0.041994  0.050028  0.045207  0.037575  0.066499  0.019496  0.060072   
4019 -0.027506 -0.103434  0.019496 -0.038755 -0.018267 -0.058038  0.054849   

          7         8         9     ...      2990      2991      2992  \
0    -0.154533 -0.082646  0.106670  ...  0.020496  0.001296  0.001742   
1    -0.088898 -0.105418 -0.028173  ...  0.047286 -0.037996 -0.084432   
2    -0.283126 -0.271070 -0.086665  ... -0.103186  0.029426  0.097294   
3    -0.021029 -0.051391 -0.043801  ...  0.118279  0.053983  0.078541   
4     0.166055  0.241068  0.243747  ...  0.125424  0.100419  0.173199   
...        ...       ...       ...  ...       ...       ...       ...   
4015  0.127563  0.107476  0.072124  ...  0.102655  0.020300 -0.054423   
4016 -0.016258 -0.013847 -0.081339  ...  0.062884  0.084577  0.071320   
4017  0.016684  0.004231  0.036771  ...  0.050832  0.105066  0.109083   
4018  0.114707  0.084577  0.024317  ...  0.010257 -0.035943 -0.031925   
4019  0.088595  0.134392  0.119528  ...  0.090202  0.056456 -0.028712   

          2993      2994      2995      2996      2997      2998      2999  
0     0.090150 -0.022815 -0.059428 -0.107651 -0.078181 -0.029959 -0.170607  
1    -0.098721 -0.040675 -0.061214 -0.095595  0.083899 -0.038889 -0.044247  
2     0.066932  0.064699  0.052197  0.115600  0.078987 -0.058535  0.045946  
3     0.112921  0.079880  0.052197  0.054876  0.053537  0.051751  0.147302  
4     0.189273  0.225440  0.186148  0.169627  0.196417  0.158018  0.100419  
...        ...       ...       ...       ...       ...       ...       ...  
4015 -0.009428 -0.007821  0.029942 -0.009428  0.004231 -0.012241 -0.016660  
4016  0.060473  0.012265  0.026728  0.033959  0.073731  0.068106  0.109083  
4017  0.071722  0.070115  0.105468  0.068508  0.101852  0.054046  0.028335  
4018 -0.035943 -0.096605 -0.197842 -0.185790 -0.231587 -0.207885 -0.170122  
4019  0.137606  0.027933  0.157693  0.079355  0.016283  0.091809  0.171352  

[4020 rows x 3000 columns]

In [ ]:
y_sub_dt=subject_466_df[3000]

In [ ]:
y_sub_dt

0       0
1       0
2       0
3       0
4       0
       ..
4015    0
4016    0
4017    0
4018    0
4019    0
Name: 3000, Length: 4020, dtype: int64

In [ ]:
y_sub_dt.value_counts()

0    2096
2     836
1     610
4     360
3     118
Name: 3000, dtype: int64

In [ ]:
x_train_sub,x_test_sub,y_train_sub,y_test_sub=train_test_split(x_sub_set,y_sub_dt,test_size=0.2,random_state=100)

In [ ]:
pip install git+https://www.github.com/keras-team/keras-contrib.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://www.github.com/keras-team/keras-contrib.git to /tmp/pip-req-build-df6e8rk1
  Running command git clone -q https://www.github.com/keras-team/keras-contrib.git /tmp/pip-req-build-df6e8rk1
  Created wheel for keras-contrib: filename=keras_contrib-2.0.8-py3-none-any.whl size=101077 sha256=4e32aa72d708eddec820fbdfc8e16db238476c6ecba9b984e144e7e9bc926a49
  Stored in directory: /tmp/pip-ephem-wheel-cache-nbr4tqpz/wheels/bb/1f/f2/b57495012683b6b20bbae94a3915ec79753111452d79886abc
Successfully built keras-contrib


In [ ]:
from keras import optimizers, losses, activations, models
from keras.layers import Dense, Input, Dropout, Convolution1D, MaxPool1D, GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from keras_contrib.layers import CRF

WINDOW_SIZE = 100

optimizer = Adam(lr=1e-4)

from scipy.stats import mode

In [ ]:
nclass = 5

#n_classes=5
def model_b(n_classes=5, use_sub_layer=False, use_rnn=True, verbose=False):
    inputLayer = Input(shape=(3000, 1), name='inLayer')
    convFine = Conv1D(filters=64, kernel_size=int(Fs/2), strides=int(Fs/16), padding='same', activation='relu', name='fConv1')(inputLayer)
    convFine = MaxPool1D(pool_size=8, strides=8, name='fMaxP1')(convFine)
    convFine = Dropout(rate=0.5, name='fDrop1')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv2')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv3')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv4')(convFine)
    convFine = MaxPool1D(pool_size=4, strides=4, name='fMaxP2')(convFine)
    fineShape = convFine.get_shape()
    convFine = Flatten(name='fFlat1')(convFine)
    
    # network to learn coarse features
    convCoarse = Conv1D(filters=32, kernel_size=Fs*4, strides=int(Fs/2), padding='same', activation='relu', name='cConv1')(inputLayer)
    convCoarse = MaxPool1D(pool_size=4, strides=4, name='cMaxP1')(convCoarse)
    convCoarse = Dropout(rate=0.5, name='cDrop1')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv2')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv3')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv4')(convCoarse)
    convCoarse = MaxPool1D(pool_size=2, strides=2, name='cMaxP2')(convCoarse)
    coarseShape = convCoarse.get_shape()
    convCoarse = Flatten(name='cFlat1')(convCoarse)
    
    # concatenate coarse and fine cnns
    mergeLayer = concatenate([convFine, convCoarse], name='merge_1')
    outLayer = Dropout(rate=0.5, name='mDrop1')(mergeLayer)
    
    outLayer = Reshape((1, outLayer.get_shape()[1]), name='reshape1')(outLayer)
    outLayer = LSTM(64, return_sequences=True)(outLayer)
    outLayer = LSTM(64, return_sequences=False)(outLayer)

    # Classify
    outLayer = Dense(n_classes, activation='softmax', name='outLayer')(outLayer)
    model = Model(inputLayer, outLayer)
    optimizer = Adam(lr=1e-4)
    model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['acc'])
    #model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
    if verbose:
        model.summary()
    return model

In [ ]:
loaded_model_shuf1=model_b(verbose=VBS)
loaded_model_shuf2=model_b(verbose=VBS)
loaded_model_shuf3=model_b(verbose=VBS)

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
5#dt_shuf1
checkpoint_path_load_model_30_epochs_shuf1 = "/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf1_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf1)
#latest_30_epochs_shuf1_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf1_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf1)

/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt


In [ ]:
#dt_shuf2
checkpoint_path_load_model_30_epochs_shuf2 = "/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf2_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf2)
#latest_300_epochs_shuf2_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf2_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf2)

/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt


In [ ]:
#dt_shuf3
checkpoint_path_load_model_30_epochs_shuf3 = "/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf3_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf3)
#latest_300_epochs_shuf3_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf3_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf3)

/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt


In [ ]:
loaded_model_shuf1.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name)

0 inLayer
1 fConv1
2 cConv1
3 fMaxP1
4 cMaxP1
5 fDrop1
6 cDrop1
7 fConv2
8 cConv2
9 fConv3
10 cConv3
11 fConv4
12 cConv4
13 fMaxP2
14 cMaxP2
15 fFlat1
16 cFlat1
17 merge_1
18 mDrop1
19 reshape1
20 lstm
21 lstm_1
22 outLayer


In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer True
1 fConv1 True
2 cConv1 True
3 fMaxP1 True
4 cMaxP1 True
5 fDrop1 True
6 cDrop1 True
7 fConv2 True
8 cConv2 True
9 fConv3 True
10 cConv3 True
11 fConv4 True
12 cConv4 True
13 fMaxP2 True
14 cMaxP2 True
15 fFlat1 True
16 cFlat1 True
17 merge_1 True
18 mDrop1 True
19 reshape1 True
20 lstm True
21 lstm_1 True
22 outLayer True


In [ ]:
for layer in loaded_model_shuf1.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf1.layers[20:]:
 # layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm False
21 lstm_1 False
22 outLayer False


In [ ]:
for layer in loaded_model_shuf2.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf2.layers[20:]:
 # layer.trainable=False

In [ ]:
for layer in loaded_model_shuf3.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf3.layers[20:]:
#  layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf2.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_2 False
21 lstm_3 False
22 outLayer False


In [ ]:
for i,layer in enumerate(loaded_model_shuf3.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_4 False
21 lstm_5 False
22 outLayer False


In [ ]:
loaded_model_shuf1.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
print(loaded_model_shuf1.summary())
print(loaded_model_shuf2.summary())
print(loaded_model_shuf3.summary())

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
x_train_sub.shape

(3216, 3000)

In [ ]:
x_train_sub

0         1         2         3         4         5         6     \
2884  0.076141  0.125956  0.148855  0.136803  0.058063  0.028736  0.037976   
3183  0.093014  0.083774  0.057661  0.030745  0.071320  0.129973  0.156488   
2680 -0.061654 -0.093391 -0.102631 -0.091382 -0.077321 -0.044379  0.002222   
352   0.017370  0.049072  0.000849 -0.013885 -0.026834  0.073629  0.066039   
2931  0.079355  0.074132  0.093014  0.079355  0.060473  0.044806  0.024317   
...        ...       ...       ...       ...       ...       ...       ...   
3927 -0.050405 -0.033532  0.013069  0.030343  0.028335  0.016684  0.073731   
3943 -0.006616 -0.006616  0.037173  0.071320  0.102655  0.082970  0.023514   
1859 -0.188914  0.020942 -0.246959 -0.030852 -0.049159  0.021835  0.018263   
2840  0.046011  0.063285  0.033557 -0.000590  0.007846  0.027933  0.023514   
1544 -0.250085  0.117833  0.128549  0.269644 -0.279554  0.193738 -0.149622   

          7         8         9     ...      2990      2991      2992  \
2884  0.042395  0.077346  0.074936  ...  0.006641  0.043601  0.064089   
3183  0.149658  0.123546  0.106673  ...  0.067705  0.046011  0.074936   
2680  0.028335 -0.037550 -0.101827  ...  0.082970  0.095826  0.053242   
352   0.019603  0.028533  0.021835  ...  0.104438  0.133014  0.101312   
2931  0.038780  0.039985  0.035566  ... -0.049602 -0.048397 -0.047191   
...        ...       ...       ...  ...       ...       ...       ...   
3927  0.016684 -0.012642 -0.014651  ... -0.002197 -0.054423 -0.057636   
3943  0.014676 -0.006616  0.031147  ...  0.131179  0.141222  0.170548   
1859 -0.022815 -0.025941  0.114707  ...  0.041481 -0.088898 -0.214811   
2840  0.025121  0.034361  0.044806  ...  0.000615  0.019496  0.043199   
1544 -0.537632 -0.150515 -0.296074  ...  0.337512  0.440207  0.382609   

          2993      2994      2995      2996      2997      2998      2999  
2884  0.076944  0.076944  0.045207  0.012667 -0.021882 -0.038755 -0.033532  
3183  0.064892  0.117921  0.116716  0.097433  0.062482  0.025924  0.005034  
2680  0.023112  0.019095  0.013470  0.037976  0.044404  0.068106  0.078551  
352   0.011565  0.018263  0.019156  0.042821 -0.033978 -0.088898 -0.026387  
2931 -0.050405 -0.037148 -0.042371 -0.066876 -0.074108 -0.068483 -0.069688  
...        ...       ...       ...       ...       ...       ...       ...  
3927 -0.064868 -0.035139  0.001418  0.055251  0.019496 -0.035943 -0.035943  
3943  0.170950  0.155684  0.146444  0.144034  0.141222  0.138008  0.160907  
1859  0.074969  0.055769 -0.110776 -0.067465 -0.246066 -0.050498 -0.079521  
2840  0.046814  0.040387  0.033557  0.030745  0.014274 -0.038353 -0.041165  
1544  0.510308  0.412078  0.554959  0.578623  0.564782  0.608539  0.600948  

[3216 rows x 3000 columns]

In [ ]:
tf.config.run_functions_eagerly(True)

In [ ]:
x_train_sub[0:500]

0         1         2         3         4         5         6     \
2884  0.076141  0.125956  0.148855  0.136803  0.058063  0.028736  0.037976   
3183  0.093014  0.083774  0.057661  0.030745  0.071320  0.129973  0.156488   
2680 -0.061654 -0.093391 -0.102631 -0.091382 -0.077321 -0.044379  0.002222   
352   0.017370  0.049072  0.000849 -0.013885 -0.026834  0.073629  0.066039   
2931  0.079355  0.074132  0.093014  0.079355  0.060473  0.044806  0.024317   
...        ...       ...       ...       ...       ...       ...       ...   
834  -0.056303 -0.097381 -0.013885 -0.065679 -0.040229 -0.038889 -0.019690   
985   0.037909 -0.004509 -0.070144 -0.089344 -0.101846 -0.094702 -0.063893   
1182 -0.059875 -0.060768 -0.001383 -0.014332  0.006207 -0.029513 -0.070591   
1105 -0.095149 -0.033978 -0.087111 -0.041122 -0.005402 -0.012099 -0.090684   
171   0.161590  0.189273  0.174985  0.171860  0.143284  0.191506  0.198650   

          7         8         9     ...      2990      2991      2992  \
2884  0.042395  0.077346  0.074936  ...  0.006641  0.043601  0.064089   
3183  0.149658  0.123546  0.106673  ...  0.067705  0.046011  0.074936   
2680  0.028335 -0.037550 -0.101827  ...  0.082970  0.095826  0.053242   
352   0.019603  0.028533  0.021835  ...  0.104438  0.133014  0.101312   
2931  0.038780  0.039985  0.035566  ... -0.049602 -0.048397 -0.047191   
...        ...       ...       ...  ...       ...       ...       ...   
834  -0.038889  0.002189  0.019603  ...  0.029872 -0.064786 -0.019243   
985  -0.046480  0.003082 -0.088898  ... -0.001383  0.110689  0.043714   
1182 -0.040229 -0.013439  0.001296  ... -0.097381 -0.089791 -0.085325   
1105 -0.084432 -0.100507 -0.055856  ...  0.055769  0.137926  0.105331   
171   0.163823  0.161144  0.154000  ...  0.111135  0.081220  0.022728   

          2993      2994      2995      2996      2997      2998      2999  
2884  0.076944  0.076944  0.045207  0.012667 -0.021882 -0.038755 -0.033532  
3183  0.064892  0.117921  0.116716  0.097433  0.062482  0.025924  0.005034  
2680  0.023112  0.019095  0.013470  0.037976  0.044404  0.068106  0.078551  
352   0.011565  0.018263  0.019156  0.042821 -0.033978 -0.088898 -0.026387  
2931 -0.050405 -0.037148 -0.042371 -0.066876 -0.074108 -0.068483 -0.069688  
...        ...       ...       ...       ...       ...       ...       ...  
834  -0.048712 -0.091130 -0.011206  0.041481  0.003975  0.049072  0.000403  
985   0.091936  0.020496  0.039249 -0.071484  0.024961  0.038802  0.160697  
1182 -0.039336 -0.024155  0.051304 -0.005402  0.058002 -0.079521 -0.133994  
1105  0.167841  0.156232  0.208473  0.174985  0.180343  0.161590  0.184362  
171  -0.006741 -0.068358 -0.114348 -0.108544 -0.111223 -0.136673 -0.129083  

[500 rows x 3000 columns]

In [ ]:
x_test_sub.shape

(804, 3000)

In [ ]:
train_dt=x_train_sub
train_dt['sleep_stage']=y_train_sub

In [ ]:
test_dt=x_test_sub
test_dt['sleep_stage']=y_test_sub

In [ ]:
train_dt.shape

(3216, 3001)

In [ ]:
test_dt.shape

(804, 3001)

In [ ]:
test_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_test_sub.csv', header=False, index=False)

In [ ]:
train_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=False, index=False)

In [ ]:
tr_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=None)

In [ ]:
tr_dt

0         1         2         3         4         5         6     \
0     0.076141  0.125956  0.148855  0.136803  0.058063  0.028736  0.037976   
1     0.093014  0.083774  0.057661  0.030745  0.071320  0.129973  0.156488   
2    -0.061654 -0.093391 -0.102631 -0.091382 -0.077321 -0.044379  0.002222   
3     0.017370  0.049072  0.000849 -0.013885 -0.026834  0.073629  0.066039   
4     0.079355  0.074132  0.093014  0.079355  0.060473  0.044806  0.024317   
...        ...       ...       ...       ...       ...       ...       ...   
3211 -0.050405 -0.033532  0.013069  0.030343  0.028335  0.016684  0.073731   
3212 -0.006616 -0.006616  0.037173  0.071320  0.102655  0.082970  0.023514   
3213 -0.188914  0.020942 -0.246959 -0.030852 -0.049159  0.021835  0.018263   
3214  0.046011  0.063285  0.033557 -0.000590  0.007846  0.027933  0.023514   
3215 -0.250085  0.117833  0.128549  0.269644 -0.279554  0.193738 -0.149622   

          7         8         9     ...      2991      2992      2993  \
0     0.042395  0.077346  0.074936  ...  0.043601  0.064089  0.076944   
1     0.149658  0.123546  0.106673  ...  0.046011  0.074936  0.064892   
2     0.028335 -0.037550 -0.101827  ...  0.095826  0.053242  0.023112   
3     0.019603  0.028533  0.021835  ...  0.133014  0.101312  0.011565   
4     0.038780  0.039985  0.035566  ... -0.048397 -0.047191 -0.050405   
...        ...       ...       ...  ...       ...       ...       ...   
3211  0.016684 -0.012642 -0.014651  ... -0.054423 -0.057636 -0.064868   
3212  0.014676 -0.006616  0.031147  ...  0.141222  0.170548  0.170950   
3213 -0.022815 -0.025941  0.114707  ... -0.088898 -0.214811  0.074969   
3214  0.025121  0.034361  0.044806  ...  0.019496  0.043199  0.046814   
3215 -0.537632 -0.150515 -0.296074  ...  0.440207  0.382609  0.510308   

          2994      2995      2996      2997      2998      2999  3000  
0     0.076944  0.045207  0.012667 -0.021882 -0.038755 -0.033532     4  
1     0.117921  0.116716  0.097433  0.062482  0.025924  0.005034     4  
2     0.019095  0.013470  0.037976  0.044404  0.068106  0.078551     1  
3     0.018263  0.019156  0.042821 -0.033978 -0.088898 -0.026387     1  
4    -0.037148 -0.042371 -0.066876 -0.074108 -0.068483 -0.069688     2  
...        ...       ...       ...       ...       ...       ...   ...  
3211 -0.035139  0.001418  0.055251  0.019496 -0.035943 -0.035943     0  
3212  0.155684  0.146444  0.144034  0.141222  0.138008  0.160907     0  
3213  0.055769 -0.110776 -0.067465 -0.246066 -0.050498 -0.079521     0  
3214  0.040387  0.033557  0.030745  0.014274 -0.038353 -0.041165     4  
3215  0.412078  0.554959  0.578623  0.564782  0.608539  0.600948     0  

[3216 rows x 3001 columns]

In [ ]:
x_sub_set=tr_dt.drop([3000],axis=1)
y_sub_dt=tr_dt[3000]

In [ ]:
y_sub_dt.value_counts()

0    1666
2     671
1     496
4     279
3     104
Name: 3000, dtype: int64

In [ ]:
y_test_sub.value_counts()

In [ ]:
loaded_model_shuf1_new=model_b(verbose=VBS)
loaded_model_shuf2_new=model_b(verbose=VBS)
loaded_model_shuf3_new=model_b(verbose=VBS)

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf1_new.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2_new.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3_new.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for layer in loaded_model_shuf1_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf1_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf2_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf2_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf3_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf3_new.layers[20:]:
  layer.trainable=True

In [ ]:
loaded_model_shuf1_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
loaded_model_shuf1_new.summary()

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf2_new.summary()

Model: "model_4"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf3_new.summary()

Model: "model_5"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

##Incremental semi-supervised learning

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

count_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)

  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)


  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)


  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)



  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)


  p1_i_fin_=np_utils.to_categorical(np.asscalar(p1_i_fin), num_classes=5)
  p2_i_fin_=np_utils.to_categorical(np.asscalar(p2_i_fin), num_classes=5)
  p3_i_fin_=np_utils.to_categorical(np.asscalar(p3_i_fin), num_classes=5)

  p1_i_fin_.shape=(1,5)
  p2_i_fin_.shape=(1,5)
  p3_i_fin_.shape=(1,5)



  

  if p1_i_inc_fin == p1_i_fin:

   
    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

  if p1_i_inc_fin != p1_i_fin:

    p1_i_inc_fin=p1_i_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

   

  
  if p2_i_inc_fin == p2_i_fin:
   
      
    
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

  if p2_i_inc_fin != p2_i_fin:

    p2_i_inc_fin=p2_i_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)


        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
  

  if p3_i_inc_fin == p3_i_fin:

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    

  if p3_i_inc_fin != p3_i_fin:

    p3_i_inc_fin=p3_i_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)


    
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     


  


In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        2.7333064e-05]], dtype=float32), array([[9.9956530e-01, 2.9518630e-04, 6.2732142e-05, 4.5667864e-05,
        3.1153173e-05]], dtype=float32), array([[5.2849718e-05, 3.2016129e-04, 9.8325461e-01, 1.4599743e-02,
        1.7727062e-03]], dtype=float32), array([[9.9951780e-01, 3.6258108e-04, 6.0660419e-05, 3.4240566e-05,
        2.4763001e-05]], dtype=float32), array([[1.3466268e-05, 4.2360649e-04, 9.9856180e-01, 7.1219640e-04,
        2.8884699e-04]], dtype=float32), array([[7.5486038e-05, 1.9209173e-03, 1.2377579e-02, 3.3353343e-05,
        9.8559266e-01]], dtype=float32), array([[9.9967802e-01, 1.9092427e-04, 5.1379026e-05, 6.5489927e-05,
        1.4238746e-05]], dtype=float32), array([[9.9320579e-01, 5.7703159e-03, 8.3486288e-04, 3.9306498e-05,
        1.4974504e-04]], dtype=float32), array([[3.9972929e-05, 1.1846983e-03, 9.9697363e-01, 6.3892156e-05,
        1.7377465e-03]], dtype=float32), array([[9.9952638e-01, 3.6044591e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8658993e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068602e-04, 9.9565065e-04, 8.5320187e-01, 1.4440058e-01,
        1.2412835e-03]], dtype=float32), array([[9.97947156e-01, 1.59555301e-03, 3.31521558e-04, 1.34054735e-05,
        1.12480004e-04]], dtype=float32), array([[2.9182529e-05, 2.3514153e-03, 9.9627328e-01, 5.0847570e-04,
        8.3760347e-04]], dtype=float32), array([[2.3999158e-03, 6.0397580e-02, 2.5356913e-01, 6.2655454e-05,
        6.8357074e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415240e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619278e-03, 1.4337271e-03, 4.3201246e-05,
        1.5281695e-04]], dtype=float32), array([[1.21958576e-04, 2.90093082e-03, 9.94503140e-01, 7.88024699e-05,
        2.39518820e-03]], dtype=float32), array([[9.9880111e-01, 4.8

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.8656351791530945

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.9572093 , 0.08053691, 0.94899536, 0.86381323, 0.75914634])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7628605483981545
Recall: 0.7219402298654993
F1 score: 0.7214947838103901
              precision    recall  f1-score   support

           0   0.986577  0.957209  0.971671      1075
           1   0.363636  0.080537  0.131868       149
           2   0.743341  0.948995  0.833673       647
           3   0.932773  0.863813  0.896970       257
           4   0.787975  0.759146  0.773292       328

    accuracy                       0.865635      2456
   macro avg   0.762861  0.721940  0.721495      2456
weighted avg   0.852554  0.865635  0.850058      2456



In [ ]:
x_train_with_semi_sup_labels=x_sub_set

In [ ]:
x_train_with_semi_sup_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_semi_sup_labels

0         1         2         3         4         5         6  \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

             7         8         9  ...      2991      2992      2993  \
0     0.129435  0.153744  0.198097  ... -0.088920 -0.118773 -0.130714   
1    -0.040524 -0.072258 -0.054247  ...  0.119858  0.074831 -0.004503   
2    -0.106993 -0.100132 -0.077833  ... -0.001501  0.037952  0.036665   
3    -0.040953 -0.046957 -0.017796  ...  0.239931  0.229639  0.205624   
4    -0.033478 -0.030919 -0.008743  ...  0.031772 -0.009596 -0.039875   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
2452 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
2453 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
2454 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
2455  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

          2994      2995      2996      2997      2998      2999  \
0    -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817   
1    -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389   
2     0.046528  0.048243  0.011364  0.021656  0.037094  0.021656   
3     0.192759  0.182039  0.137869  0.111710  0.105278  0.122860   
4    -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919   
...        ...       ...       ...       ...       ...       ...   
2451  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852   
2452 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376   
2453 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225   
2454  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663   
2455  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273   

      pseudo_labels  
0                 2  
1                 2  
2                 4  
3                 2  
4                 2  
...             ...  
2451              0  
2452              0  
2453              1  
2454              2  
2455              2  

[2456 rows x 3001 columns]

In [ ]:
x_train_with_semi_sup_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_inc_semi_sup_labels_train_on_batch_trial_4.csv', header=False, index=False)

In [ ]:
#classic incremental learning, not semi supervised inc

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:3216]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
    
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  

  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  

  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  
    
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  



  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)



  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)


  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

   

  

  loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

  

  loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

  

  loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)




In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 4, 0, 0, 2, 1, 0, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 1, 2, 0, 2, 2, 4, 0, 2, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 1, 0, 3, 0, 0, 0, 4, 0, 1, 1, 0, 2, 2, 0, 2, 0, 0, 2, 1, 0, 0, 2, 2, 2, 0, 0, 1, 0, 3, 3, 0, 1, 1, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 0, 2, 2, 1, 0, 0, 0, 0, 0, 2, 0, 0, 3, 2, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 2, 0, 2, 0, 3, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 0, 3, 2, 0, 2, 1, 2, 0, 2, 2, 2, 0, 0, 0, 4, 0, 2, 0, 2, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 2, 2, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 2, 0, 0, 0, 0, 0, 1, 2, 0, 1, 0, 0, 2, 2, 0, 3, 0, 3, 4, 2, 0, 1, 0, 2, 2, 3, 0, 4, 3, 0, 2, 0, 2, 2, 3, 0, 0, 1, 0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 4, 0, 0, 1, 0, 0, 1, 2, 2, 4, 0, 0, 0, 0, 0, 0, 3, 2, 0, 0, 0, 2, 2, 0, 2, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 2, 2, 2, 0, 2, 0, 0, 3, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 4, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 0, 2, 2, 0, 0, 1, 0, 2, 0, 0, 2, 2, 3, 1, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        2.3550448e-01]], dtype=float32), array([[2.9867890e-04, 9.9775451e-01, 1.6392566e-03, 4.7465605e-06,
        3.0284788e-04]], dtype=float32), array([[2.0653957e-04, 9.9334478e-01, 6.1433148e-03, 5.5050696e-06,
        2.9984457e-04]], dtype=float32), array([[4.2604408e-03, 9.8429316e-01, 3.2198364e-03, 7.9099555e-06,
        8.2187019e-03]], dtype=float32), array([[1.1364576e-04, 9.7779578e-01, 2.1515934e-02, 1.0895513e-05,
        5.6372402e-04]], dtype=float32), array([[2.4207895e-06, 3.0936487e-04, 9.9864548e-01, 8.1245566e-04,
        2.3020279e-04]], dtype=float32), array([[5.0449010e-02, 9.4478220e-01, 2.5317520e-03, 2.2481327e-05,
        2.2145011e-03]], dtype=float32), array([[2.6324592e-04, 9.9648643e-01, 3.0883399e-03, 7.3829983e-06,
        1.5471563e-04]], dtype=float32), array([[1.0634041e-04, 9.8211229e-01, 1.7058942e-02, 5.6572894e-06,
        7.1686646e-04]], dtype=float32), array([[8.0962709e-06, 9.2608680e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        8.69284630e-01]], dtype=float32), array([[9.6976960e-01, 2.3223983e-02, 3.4924690e-03, 3.9525330e-05,
        3.4744004e-03]], dtype=float32), array([[9.9942517e-01, 3.7063993e-04, 1.7700935e-04, 1.5346863e-05,
        1.1738446e-05]], dtype=float32), array([[9.97308731e-01, 1.23971794e-03, 1.58012263e-04, 1.34727725e-05,
        1.28008612e-03]], dtype=float32), array([[9.9663937e-01, 1.9175994e-03, 1.3227750e-03, 5.3991302e-05,
        6.6315690e-05]], dtype=float32), array([[1.0806796e-04, 8.0214028e-04, 8.7063915e-01, 1.2544917e-01,
        3.0014655e-03]], dtype=float32), array([[9.9983037e-01, 8.9574227e-05, 2.2254088e-05, 4.4507648e-05,
        1.3261608e-05]], dtype=float32), array([[9.9505842e-01, 3.6415600e-03, 1.1930006e-03, 4.7521196e-05,
        5.9499635e-05]], dtype=float32), array([[9.8930615e-01, 6.9356803e-03, 2.8645883e-03, 9.4122779e-06,
        8.8411622e-04]], dtype=float32), array([[0.00142889, 0.00790611

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote_inc)

0.396455223880597

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote)

0.8050373134328358

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.257503  , 0.09879032, 0.99850969, 0.02884615, 0.44444444])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.5821678113348894
Recall: 0.36561872182120014
F1 score: 0.31581824748651277
              precision    recall  f1-score   support

           0   0.875510  0.257503  0.397959      1666
           1   0.331081  0.098790  0.152174       496
           2   0.280335  0.998510  0.437765       671
           3   0.750000  0.028846  0.055556       104
           4   0.673913  0.444444  0.535637       279

    accuracy                       0.396455      3216
   macro avg   0.582168  0.365619  0.315818      3216
weighted avg   0.645815  0.396455  0.369229      3216



In [ ]:
x_train_classic_labels=x_sub_set

In [ ]:
x_train_classic_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_classic_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_classic_labels_trial_10.csv', header=False, index=False)

## simple incremental tri-training 

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:3216]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  #if (p1_i_inc_fin != p1_i_fin):
   # p1_i_inc_fin=p1_i_fin

  #if (p2_i_inc_fin != p2_i_fin):
   # p2_i_inc_fin=p2_i_fin

  #if (p3_i_inc_fin != p3_i_fin):
   # p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 4, 0, 0, 2, 1, 0, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 1, 2, 0, 2, 2, 4, 0, 2, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 1, 0, 3, 0, 0, 0, 4, 0, 1, 1, 0, 2, 2, 0, 2, 0, 0, 2, 1, 0, 0, 2, 2, 2, 0, 0, 1, 0, 3, 3, 0, 1, 1, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 0, 2, 2, 1, 0, 0, 0, 0, 0, 2, 0, 0, 3, 2, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 2, 0, 2, 0, 3, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 0, 3, 2, 0, 2, 1, 2, 0, 2, 2, 2, 0, 0, 0, 4, 0, 2, 0, 2, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 2, 2, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 2, 0, 0, 0, 0, 0, 1, 2, 0, 1, 0, 0, 2, 2, 0, 3, 0, 3, 4, 2, 0, 1, 0, 2, 2, 3, 0, 4, 3, 0, 2, 0, 2, 2, 3, 0, 0, 1, 0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 4, 0, 0, 1, 0, 0, 1, 2, 2, 4, 0, 0, 0, 0, 0, 0, 3, 2, 0, 0, 0, 2, 2, 0, 2, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 2, 2, 2, 0, 2, 0, 0, 3, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 4, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 0, 2, 2, 0, 0, 1, 0, 2, 0, 0, 2, 2, 3, 1, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        2.3166478e-01]], dtype=float32), array([[3.0117182e-04, 9.9829096e-01, 1.0817314e-03, 2.5438408e-06,
        3.2359772e-04]], dtype=float32), array([[4.9620605e-04, 9.9052584e-01, 8.7831244e-03, 5.9065060e-06,
        1.8887331e-04]], dtype=float32), array([[6.7315861e-03, 9.8794878e-01, 2.1121684e-03, 4.1031972e-06,
        3.2034153e-03]], dtype=float32), array([[1.4108927e-04, 9.7930658e-01, 2.0198474e-02, 5.2125552e-06,
        3.4855484e-04]], dtype=float32), array([[2.5498452e-06, 2.1782028e-04, 9.9878353e-01, 8.2081294e-04,
        1.7527959e-04]], dtype=float32), array([[1.9864033e-01, 7.9790652e-01, 2.8871535e-03, 5.1421877e-05,
        5.1454722e-04]], dtype=float32), array([[1.8906390e-04, 9.9642986e-01, 3.2167155e-03, 3.9982706e-06,
        1.6037306e-04]], dtype=float32), array([[2.9200985e-04, 9.8334920e-01, 1.5903365e-02, 6.2719205e-06,
        4.4908246e-04]], dtype=float32), array([[9.1383799e-06, 8.1105687e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        8.6928475e-01]], dtype=float32), array([[9.6976960e-01, 2.3223968e-02, 3.4924673e-03, 3.9525257e-05,
        3.4744004e-03]], dtype=float32), array([[9.9942517e-01, 3.7063978e-04, 1.7700935e-04, 1.5346863e-05,
        1.1738446e-05]], dtype=float32), array([[9.9730873e-01, 1.2397168e-03, 1.5801210e-04, 1.3472747e-05,
        1.2800850e-03]], dtype=float32), array([[9.9663937e-01, 1.9176002e-03, 1.3227757e-03, 5.3991353e-05,
        6.6315755e-05]], dtype=float32), array([[1.0806796e-04, 8.0214028e-04, 8.7063915e-01, 1.2544921e-01,
        3.0014641e-03]], dtype=float32), array([[9.9983037e-01, 8.9574140e-05, 2.2254066e-05, 4.4507600e-05,
        1.3261594e-05]], dtype=float32), array([[9.9505842e-01, 3.6415600e-03, 1.1930000e-03, 4.7521196e-05,
        5.9499580e-05]], dtype=float32), array([[9.8930615e-01, 6.9356831e-03, 2.8645894e-03, 9.4122779e-06,
        8.8411663e-04]], dtype=float32), array([[0.00142889, 0.00790611, 0.41

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote_inc)

0.4085820895522388

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote)

0.8050373134328358

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.18667467, 0.71370968, 0.95529061, 0.02884615, 0.01792115])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7153750942544119
Recall: 0.38048845182303537
F1 score: 0.2985512430975068
              precision    recall  f1-score   support

           0   0.956923  0.186675  0.312406      1666
           1   0.181445  0.713710  0.289334       496
           2   0.688507  0.955291  0.800250       671
           3   0.750000  0.028846  0.055556       104
           4   1.000000  0.017921  0.035211       279

    accuracy                       0.408582      3216
   macro avg   0.715375  0.380488  0.298551      3216
weighted avg   0.778364  0.408582  0.378280      3216



In [ ]:
x_train_with_simple_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_simple_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_simple_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_simple_tri_trained_labels_frozen_layers_train_on_batch_trial_10.csv', header=False, index=False)

##Incremental semi supervised Learning with Tri-Training, majority voting (final modified code)

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:3216]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  if (p1_i_inc_fin != p1_i_fin):
    p1_i_inc_fin=p1_i_fin

  if (p2_i_inc_fin != p2_i_fin):
    p2_i_inc_fin=p2_i_fin

  if (p3_i_inc_fin != p3_i_fin):
    p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 4, 0, 0, 2, 1, 0, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 1, 2, 0, 2, 2, 4, 0, 2, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 1, 0, 3, 0, 0, 0, 4, 0, 1, 1, 0, 2, 2, 0, 2, 0, 0, 2, 1, 0, 0, 2, 2, 2, 0, 0, 1, 0, 3, 3, 0, 1, 1, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 0, 2, 2, 1, 0, 0, 0, 0, 0, 2, 0, 0, 3, 2, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 2, 0, 2, 0, 3, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 0, 3, 2, 0, 2, 1, 2, 0, 2, 2, 2, 0, 0, 0, 4, 0, 2, 0, 2, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 2, 2, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 2, 0, 0, 0, 0, 0, 1, 2, 0, 1, 0, 0, 2, 2, 0, 3, 0, 3, 4, 2, 0, 1, 0, 2, 2, 3, 0, 4, 3, 0, 2, 0, 2, 2, 3, 0, 0, 1, 0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 4, 0, 0, 1, 0, 0, 1, 2, 2, 4, 0, 0, 0, 0, 0, 0, 3, 2, 0, 0, 0, 2, 2, 0, 2, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 2, 2, 2, 0, 2, 0, 0, 3, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 4, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 0, 2, 2, 0, 0, 1, 0, 2, 0, 0, 2, 2, 3, 1, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        9.3280631e-01]], dtype=float32), array([[9.9552464e-01, 3.9616758e-03, 2.1253963e-04, 4.2351207e-05,
        2.5884813e-04]], dtype=float32), array([[9.9954468e-01, 3.5295144e-04, 8.3282037e-05, 1.0367429e-05,
        8.7134567e-06]], dtype=float32), array([[9.9905282e-01, 5.7643943e-04, 3.1736705e-05, 2.0021111e-05,
        3.1888080e-04]], dtype=float32), array([[9.9726284e-01, 2.0831362e-03, 5.4076954e-04, 7.0249953e-05,
        4.2969932e-05]], dtype=float32), array([[1.0972318e-05, 2.2064292e-04, 9.6978474e-01, 2.9167050e-02,
        8.1663905e-04]], dtype=float32), array([[9.9985754e-01, 7.1319548e-05, 1.6731268e-05, 4.6048237e-05,
        8.3655341e-06]], dtype=float32), array([[9.9695849e-01, 2.5325110e-03, 4.3089862e-04, 4.6829326e-05,
        3.1237625e-05]], dtype=float32), array([[9.9881881e-01, 9.2437980e-04, 1.9456880e-04, 1.0197077e-05,
        5.2053299e-05]], dtype=float32), array([[2.0823088e-04, 1.9137019e-03

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        8.69284630e-01]], dtype=float32), array([[9.6976960e-01, 2.3223968e-02, 3.4924673e-03, 3.9525294e-05,
        3.4743987e-03]], dtype=float32), array([[9.9942517e-01, 3.7063993e-04, 1.7700935e-04, 1.5346863e-05,
        1.1738446e-05]], dtype=float32), array([[9.97308731e-01, 1.23971736e-03, 1.58012102e-04, 1.34727725e-05,
        1.28008495e-03]], dtype=float32), array([[9.9663937e-01, 1.9175984e-03, 1.3227750e-03, 5.3991251e-05,
        6.6315690e-05]], dtype=float32), array([[1.0806796e-04, 8.0214109e-04, 8.7063915e-01, 1.2544923e-01,
        3.0014671e-03]], dtype=float32), array([[9.9983037e-01, 8.9574227e-05, 2.2254088e-05, 4.4507648e-05,
        1.3261620e-05]], dtype=float32), array([[9.9505842e-01, 3.6415618e-03, 1.1930006e-03, 4.7521196e-05,
        5.9499580e-05]], dtype=float32), array([[9.8930627e-01, 6.9356672e-03, 2.8645818e-03, 9.4122788e-06,
        8.8411418e-04]], dtype=float32), array([[0.00142889, 0.00790611

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote_inc)

0.8103233830845771

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:3216], m_vote)

0.8050373134328358

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.96698679, 0.31854839, 0.88077496, 0.84615385, 0.56630824])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7321428717455735
Recall: 0.7157544468876564
F1 score: 0.7118697453589073
              precision    recall  f1-score   support

           0   0.875068  0.966987  0.918734      1666
           1   0.533784  0.318548  0.398990       496
           2   0.790107  0.880775  0.832981       671
           3   0.671756  0.846154  0.748936       104
           4   0.790000  0.566308  0.659708       279

    accuracy                       0.810323      3216
   macro avg   0.732143  0.715754  0.711870      3216
weighted avg   0.790751  0.810323  0.792720      3216



In [ ]:
x_sub_set

0         1         2         3         4         5         6     \
0     0.076141  0.125956  0.148855  0.136803  0.058063  0.028736  0.037976   
1     0.093014  0.083774  0.057661  0.030745  0.071320  0.129973  0.156488   
2    -0.061654 -0.093391 -0.102631 -0.091382 -0.077321 -0.044379  0.002222   
3     0.017370  0.049072  0.000849 -0.013885 -0.026834  0.073629  0.066039   
4     0.079355  0.074132  0.093014  0.079355  0.060473  0.044806  0.024317   
...        ...       ...       ...       ...       ...       ...       ...   
3211 -0.050405 -0.033532  0.013069  0.030343  0.028335  0.016684  0.073731   
3212 -0.006616 -0.006616  0.037173  0.071320  0.102655  0.082970  0.023514   
3213 -0.188914  0.020942 -0.246959 -0.030852 -0.049159  0.021835  0.018263   
3214  0.046011  0.063285  0.033557 -0.000590  0.007846  0.027933  0.023514   
3215 -0.250085  0.117833  0.128549  0.269644 -0.279554  0.193738 -0.149622   

          7         8         9     ...      2990      2991      2992  \
0     0.042395  0.077346  0.074936  ...  0.006641  0.043601  0.064089   
1     0.149658  0.123546  0.106673  ...  0.067705  0.046011  0.074936   
2     0.028335 -0.037550 -0.101827  ...  0.082970  0.095826  0.053242   
3     0.019603  0.028533  0.021835  ...  0.104438  0.133014  0.101312   
4     0.038780  0.039985  0.035566  ... -0.049602 -0.048397 -0.047191   
...        ...       ...       ...  ...       ...       ...       ...   
3211  0.016684 -0.012642 -0.014651  ... -0.002197 -0.054423 -0.057636   
3212  0.014676 -0.006616  0.031147  ...  0.131179  0.141222  0.170548   
3213 -0.022815 -0.025941  0.114707  ...  0.041481 -0.088898 -0.214811   
3214  0.025121  0.034361  0.044806  ...  0.000615  0.019496  0.043199   
3215 -0.537632 -0.150515 -0.296074  ...  0.337512  0.440207  0.382609   

          2993      2994      2995      2996      2997      2998      2999  
0     0.076944  0.076944  0.045207  0.012667 -0.021882 -0.038755 -0.033532  
1     0.064892  0.117921  0.116716  0.097433  0.062482  0.025924  0.005034  
2     0.023112  0.019095  0.013470  0.037976  0.044404  0.068106  0.078551  
3     0.011565  0.018263  0.019156  0.042821 -0.033978 -0.088898 -0.026387  
4    -0.050405 -0.037148 -0.042371 -0.066876 -0.074108 -0.068483 -0.069688  
...        ...       ...       ...       ...       ...       ...       ...  
3211 -0.064868 -0.035139  0.001418  0.055251  0.019496 -0.035943 -0.035943  
3212  0.170950  0.155684  0.146444  0.144034  0.141222  0.138008  0.160907  
3213  0.074969  0.055769 -0.110776 -0.067465 -0.246066 -0.050498 -0.079521  
3214  0.046814  0.040387  0.033557  0.030745  0.014274 -0.038353 -0.041165  
3215  0.510308  0.412078  0.554959  0.578623  0.564782  0.608539  0.600948  

[3216 rows x 3000 columns]

In [ ]:
x_train_with_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_tri_trained_labels

0         1         2         3         4         5         6  \
0     0.076141  0.125956  0.148855  0.136803  0.058063  0.028736  0.037976   
1     0.093014  0.083774  0.057661  0.030745  0.071320  0.129973  0.156488   
2    -0.061654 -0.093391 -0.102631 -0.091382 -0.077321 -0.044379  0.002222   
3     0.017370  0.049072  0.000849 -0.013885 -0.026834  0.073629  0.066039   
4     0.079355  0.074132  0.093014  0.079355  0.060473  0.044806  0.024317   
...        ...       ...       ...       ...       ...       ...       ...   
3211 -0.050405 -0.033532  0.013069  0.030343  0.028335  0.016684  0.073731   
3212 -0.006616 -0.006616  0.037173  0.071320  0.102655  0.082970  0.023514   
3213 -0.188914  0.020942 -0.246959 -0.030852 -0.049159  0.021835  0.018263   
3214  0.046011  0.063285  0.033557 -0.000590  0.007846  0.027933  0.023514   
3215 -0.250085  0.117833  0.128549  0.269644 -0.279554  0.193738 -0.149622   

             7         8         9  ...      2991      2992      2993  \
0     0.042395  0.077346  0.074936  ...  0.043601  0.064089  0.076944   
1     0.149658  0.123546  0.106673  ...  0.046011  0.074936  0.064892   
2     0.028335 -0.037550 -0.101827  ...  0.095826  0.053242  0.023112   
3     0.019603  0.028533  0.021835  ...  0.133014  0.101312  0.011565   
4     0.038780  0.039985  0.035566  ... -0.048397 -0.047191 -0.050405   
...        ...       ...       ...  ...       ...       ...       ...   
3211  0.016684 -0.012642 -0.014651  ... -0.054423 -0.057636 -0.064868   
3212  0.014676 -0.006616  0.031147  ...  0.141222  0.170548  0.170950   
3213 -0.022815 -0.025941  0.114707  ... -0.088898 -0.214811  0.074969   
3214  0.025121  0.034361  0.044806  ...  0.019496  0.043199  0.046814   
3215 -0.537632 -0.150515 -0.296074  ...  0.440207  0.382609  0.510308   

          2994      2995      2996      2997      2998      2999  \
0     0.076944  0.045207  0.012667 -0.021882 -0.038755 -0.033532   
1     0.117921  0.116716  0.097433  0.062482  0.025924  0.005034   
2     0.019095  0.013470  0.037976  0.044404  0.068106  0.078551   
3     0.018263  0.019156  0.042821 -0.033978 -0.088898 -0.026387   
4    -0.037148 -0.042371 -0.066876 -0.074108 -0.068483 -0.069688   
...        ...       ...       ...       ...       ...       ...   
3211 -0.035139  0.001418  0.055251  0.019496 -0.035943 -0.035943   
3212  0.155684  0.146444  0.144034  0.141222  0.138008  0.160907   
3213  0.055769 -0.110776 -0.067465 -0.246066 -0.050498 -0.079521   
3214  0.040387  0.033557  0.030745  0.014274 -0.038353 -0.041165   
3215  0.412078  0.554959  0.578623  0.564782  0.608539  0.600948   

      pseudo_labels  
0                 2  
1                 4  
2                 0  
3                 0  
4                 2  
...             ...  
3211              0  
3212              0  
3213              0  
3214              4  
3215              0  

[3216 rows x 3001 columns]

In [ ]:
x_train_with_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_5.csv', header=False, index=False)

appending the subject specific (train data,tri-trained labels) to the (transfer set, maj_labels) 

In [ ]:
transfer_set=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_50_subs.csv',header=None)

In [ ]:
sub_set_with_semi_sup_tri_trained_labels=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_3.csv',header=None)

In [ ]:
transfer_set_new=transfer_set.append(sub_set_with_semi_sup_tri_trained_labels, ignore_index=True)

In [ ]:
transfer_set_new.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_466_trial_3.csv', header=False, index=False)

In [ ]:
transfer_dt_plus_sub_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_466_trial_3.csv',header=None)

In [ ]:
transfer_dt_plus_sub_dt

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
119929 -0.050405 -0.033532  0.013069  0.030343  0.028335  0.016684  0.073731   
119930 -0.006616 -0.006616  0.037173  0.071320  0.102655  0.082970  0.023514   
119931 -0.188914  0.020942 -0.246959 -0.030852 -0.049159  0.021835  0.018263   
119932  0.046011  0.063285  0.033557 -0.000590  0.007846  0.027933  0.023514   
119933 -0.250085  0.117833  0.128549  0.269644 -0.279554  0.193738 -0.149622   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
119929  0.016684 -0.012642 -0.014651  ... -0.054423 -0.057636 -0.064868   
119930  0.014676 -0.006616  0.031147  ...  0.141222  0.170548  0.170950   
119931 -0.022815 -0.025941  0.114707  ... -0.088898 -0.214811  0.074969   
119932  0.025121  0.034361  0.044806  ...  0.019496  0.043199  0.046814   
119933 -0.537632 -0.150515 -0.296074  ...  0.440207  0.382609  0.510308   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
119929 -0.035139  0.001418  0.055251  0.019496 -0.035943 -0.035943     0  
119930  0.155684  0.146444  0.144034  0.141222  0.138008  0.160907     0  
119931  0.055769 -0.110776 -0.067465 -0.246066 -0.050498 -0.079521     0  
119932  0.040387  0.033557  0.030745  0.014274 -0.038353 -0.041165     4  
119933  0.412078  0.554959  0.578623  0.564782  0.608539  0.600948     0  

[119934 rows x 3001 columns]

In [ ]:
transfer_set

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
116713  0.032558  0.033944  0.046413  0.056111  0.060267  0.066271  0.077816   
116714  0.068695  0.059483  0.051071  0.044662  0.037051  0.041057  0.040656   
116715  0.013392  0.030717  0.029805  0.016127  0.026613  0.024334  0.019775   
116716 -0.057457 -0.065629 -0.101198 -0.114176 -0.141093 -0.184354 -0.222807   
116717 -0.065742 -0.082698 -0.086365 -0.053368 -0.023122 -0.024038 -0.046494   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
116713  0.058882  0.078278  0.051493  ...  0.024707  0.025631  0.015933   
116714  0.046264  0.039054  0.045063  ...  0.035850  0.031444  0.026637   
116715  0.038012  0.027069  0.031629  ...  0.013392  0.018863  0.034820   
116716 -0.230017 -0.242514 -0.231459  ... -0.085817 -0.068993 -0.058899   
116717 -0.133109 -0.211476 -0.300383  ... -0.135401 -0.128985 -0.091864   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
116713  0.044565 -0.000231  0.018242 -0.028402  0.021475  0.028402     2  
116714  0.023433  0.027839  0.023833  0.018626  0.005007  0.007010     4  
116715  0.034364  0.042115  0.045306  0.041659  0.032996  0.024334     4  
116716 -0.043999 -0.058419 -0.065629 -0.070916 -0.068513 -0.090143     2  
116717 -0.071700 -0.102404 -0.157398 -0.150524 -0.087281 -0.042828     2  

[116718 rows x 3001 columns]

trial 2,3...